In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/spaceship-titanic/sample_submission.csv
/kaggle/input/spaceship-titanic/train.csv
/kaggle/input/spaceship-titanic/test.csv


# Install Packages
# Paketleri Kur

In [2]:
!pip install fasteda -q
!pip install pandas_profiling

/bin/bash: /opt/conda/lib/libtinfo.so.6: no version information available (required by /bin/bash)
/bin/bash: /opt/conda/lib/libtinfo.so.6: no version information available (required by /bin/bash)
  Attempting uninstall: markupsafe
    Found existing installation: MarkupSafe 2.1.2
    Uninstalling MarkupSafe-2.1.2:
      Successfully uninstalled MarkupSafe-2.1.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
werkzeug 2.2.2 requires MarkupSafe>=2.1.1, but you have markupsafe 2.0.1 which is incompatible.
tensorboard 2.9.1 requires protobuf<3.20,>=3.9.2, but you have protobuf 3.20.3 which is incompatible.


In [3]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from scipy import stats
import warnings
warnings.filterwarnings("ignore")
%matplotlib inline
sns.set(style="darkgrid",font_scale=1.5)
pd.set_option("display.max.columns",None)
from fasteda import fast_eda
from pandas_profiling import ProfileReport

# Let's explore data quickly with Fast Eda and Pandas Profiling Libraries
# Fast Eda ve Pandas Profiling Kütüphaneleri ile verileri hızlı bir şekilde keşfedelim

In [4]:
train = pd.read_csv("/kaggle/input/spaceship-titanic/train.csv")

In [5]:
train_profile = ProfileReport(train, title="train")
train_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [6]:
test = pd.read_csv("/kaggle/input/spaceship-titanic/test.csv")

In [7]:
test_profile = ProfileReport(test, title="test")
test_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# Missing Values
# Eksik Değerler

## Replacing categorical value with mode and numerical values with median
## Kategorik değeri modla ve sayısal değerleri medyanla değiştirme


In [8]:
cat_col = ['HomePlanet', 'CryoSleep', 'Cabin', 'Destination', 'VIP']
mode = train[cat_col].mode().iloc[0]
train[cat_col] = train[cat_col].fillna(mode)

In [9]:
mode = test[cat_col].mode().iloc[0]
test[cat_col] = test[cat_col].fillna(mode)

## Doing the same with the test set
## Test seti ile aynı şeyi yapmak

In [10]:
num_col = ['Age', 'FoodCourt', 'RoomService', 'ShoppingMall', 'Spa', 'VRDeck']
med = train[num_col].median()
train[num_col] = train[num_col].fillna(med)

In [11]:
med = test[num_col].median()
test[num_col] = test[num_col].fillna(med)

In [12]:
Total = train.isnull().sum().sort_values(ascending=False)
percent = (train.isnull().sum() / train.isnull().count()).sort_values(ascending=False)
missing_data = pd.concat([Total, percent], axis=1, keys=['Total', 'Percent'])
missing_data.head(25)

Total   Percent
Name            200  0.023007
PassengerId       0  0.000000
HomePlanet        0  0.000000
CryoSleep         0  0.000000
Cabin             0  0.000000
Destination       0  0.000000
Age               0  0.000000
VIP               0  0.000000
RoomService       0  0.000000
FoodCourt         0  0.000000
ShoppingMall      0  0.000000
Spa               0  0.000000
VRDeck            0  0.000000
Transported       0  0.000000

In [13]:
Total = test.isnull().sum().sort_values(ascending=False)
percent = (test.isnull().sum() / test.isnull().count()).sort_values(ascending=False)
missing_data = pd.concat([Total, percent], axis=1, keys=['Total', 'Percent'])
missing_data.head(25)

Total   Percent
Name             94  0.021978
PassengerId       0  0.000000
HomePlanet        0  0.000000
CryoSleep         0  0.000000
Cabin             0  0.000000
Destination       0  0.000000
Age               0  0.000000
VIP               0  0.000000
RoomService       0  0.000000
FoodCourt         0  0.000000
ShoppingMall      0  0.000000
Spa               0  0.000000
VRDeck            0  0.000000

In [14]:
train.drop(columns=['Name'],inplace=True)

In [15]:
test.drop(columns=['Name'],inplace=True)

In [16]:
train.head()

PassengerId HomePlanet  CryoSleep  Cabin  Destination   Age    VIP  \
0     0001_01     Europa      False  B/0/P  TRAPPIST-1e  39.0  False   
1     0002_01      Earth      False  F/0/S  TRAPPIST-1e  24.0  False   
2     0003_01     Europa      False  A/0/S  TRAPPIST-1e  58.0   True   
3     0003_02     Europa      False  A/0/S  TRAPPIST-1e  33.0  False   
4     0004_01      Earth      False  F/1/S  TRAPPIST-1e  16.0  False   

   RoomService  FoodCourt  ShoppingMall     Spa  VRDeck  Transported  
0          0.0        0.0           0.0     0.0     0.0        False  
1        109.0        9.0          25.0   549.0    44.0         True  
2         43.0     3576.0           0.0  6715.0    49.0        False  
3          0.0     1283.0         371.0  3329.0   193.0        False  
4        303.0       70.0         151.0   565.0     2.0         True

In [17]:
test.head()

PassengerId HomePlanet  CryoSleep  Cabin  Destination   Age    VIP  \
0     0013_01      Earth       True  G/3/S  TRAPPIST-1e  27.0  False   
1     0018_01      Earth      False  F/4/S  TRAPPIST-1e  19.0  False   
2     0019_01     Europa       True  C/0/S  55 Cancri e  31.0  False   
3     0021_01     Europa      False  C/1/S  TRAPPIST-1e  38.0  False   
4     0023_01      Earth      False  F/5/S  TRAPPIST-1e  20.0  False   

   RoomService  FoodCourt  ShoppingMall     Spa  VRDeck  
0          0.0        0.0           0.0     0.0     0.0  
1          0.0        9.0           0.0  2823.0     0.0  
2          0.0        0.0           0.0     0.0     0.0  
3          0.0     6652.0           0.0   181.0   585.0  
4         10.0        0.0         635.0     0.0     0.0

# Model Prediction Algorithm
# Model Tahmin Algoritması

In [18]:
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder
from sklearn.metrics import mean_absolute_error
import pandas as pd
import numpy as np
import base64
import seaborn as sns
import matplotlib.pyplot as plt
import os
import random
import gc

from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import StandardScaler
from sklearn.utils import shuffle
from sklearn.model_selection import train_test_split
from sklearn.utils import shuffle
from sklearn.metrics import log_loss
from sklearn.metrics import accuracy_score
import optuna
import xgboost as xgb
from sklearn.ensemble import (RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier, 
                              ExtraTreesClassifier, VotingClassifier)
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.neural_network import MLPClassifier
from catboost import CatBoostClassifier
from sklearn.svm import SVC
from sklearn import datasets, linear_model
import lightgbm as lgb
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import StratifiedKFold

pd.set_option('display.max_columns', None)   

from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
import eli5
from eli5.sklearn import PermutationImportance

In [19]:
test = pd.read_csv('/kaggle/input/spaceship-titanic/test.csv')
sample = pd.read_csv('/kaggle/input/spaceship-titanic/sample_submission.csv')
train = pd.read_csv('/kaggle/input/spaceship-titanic/train.csv')

# Preprocessing
# Ön İşleme

In [20]:
def get_score(model,X,y):
    n = cross_val_score(model,X,y,scoring ='accuracy',cv=20)
    return n

In [21]:
params_XGB_best ={'lambda': 3.0610042624477543, 
             'alpha': 4.581902571574289, 
             'colsample_bytree': 0.9241969052729379, 
             'subsample': 0.9527591724824661, 
             'learning_rate': 0.06672065863100594, 
             'n_estimators': 725, #initial value is 651
             'max_depth': 5, 
             'min_child_weight': 1, 
             'num_parallel_tree': 1}

In [22]:
def t_fold(X,y,n_splits): 
    params= {'lambda': 3.0610042624477543, 
             'alpha': 4.581902571574289, 
             'colsample_bytree': 0.9241969052729379, 
             'subsample': 0.9527591724824661, 
             'learning_rate': 0.06672065863100594, 
             'n_estimators': 7250, #initial value is 725
             'max_depth': 5, 
             'min_child_weight': 1, 
             'num_parallel_tree': 1,
             'early_stopping_rounds':200,}
    results=[]
    n_iterations=[]
    skf = StratifiedKFold(n_splits=n_splits)
    for train_index, test_index in skf.split(X, y):
        train_X, valid_X = X.iloc[train_index], X.iloc[test_index]
        train_y, valid_y = y.iloc[train_index], y.iloc[test_index]
        model = xgb.XGBClassifier(**params).fit(train_X,train_y,
                                      eval_set=[(valid_X,valid_y)],
                                      verbose=0
                                     )  
        n_iteration = model.get_booster().best_iteration
        n_iterations.append(n_iteration)
        result = accuracy_score(valid_y,(model.predict(valid_X)))
        results.append(result)
        i=int(sum(n_iterations)/len(n_iterations))
    print("Average n_ite=" + str(i))
    print("% of scatter =" + str(np.std(n_iterations)/i))    
    n=sum(results)/len(results) 
    print (n)
    print("FIIINISH__________________________________\n")
    return n

In [23]:
train_test=train.append(test)

In [24]:
print(train_test.isnull().sum())
sns.heatmap(train_test.isnull())

PassengerId        0
HomePlanet       288
CryoSleep        310
Cabin            299
Destination      274
Age              270
VIP              296
RoomService      263
FoodCourt        289
ShoppingMall     306
Spa              284
VRDeck           268
Name             294
Transported     4277
dtype: int64


<AxesSubplot:>

### Expenses+CryoSleep
### Harcamalar+CryoSleep

In [25]:
Expenses_columns = ['RoomService','FoodCourt','ShoppingMall','Spa','VRDeck']

In [26]:
train_test.loc[:,Expenses_columns]=train_test.apply(lambda x: 0 if x.CryoSleep == True else x,axis =1)

### CryoSleep + Expenses
### CryoSleep + Masraflar

In [27]:
train_test['Expenses'] = train_test.loc[:,Expenses_columns].sum(axis=1)

In [28]:
train_test.loc[:,['CryoSleep']]=train_test.apply(lambda x: True if x.Expenses == 0 and pd.isna(x.CryoSleep) else x,axis =1)

### Name
### İsim

In [29]:
train_test.Name = train_test.Name.fillna('Unknown Unknown')

### Cabin

### Here I want to create handbooks to fill in informations in Cabin, VIP status, HomePlanet and Destination.
### Burada Kabin, VIP durumu, Ana Gezegen ve Varış Noktasındaki bilgileri doldurmak için el kitapları oluşturmak istiyorum.


In [30]:
train_test.loc[:,['Room']] = train_test.PassengerId.apply(lambda x: x[0:4] )

In [31]:

guide_VIP=train_test.loc[:,['Room','VIP']].dropna().drop_duplicates('Room')
guide_Cabin=train_test.loc[:,['Room','Cabin']].dropna().drop_duplicates('Room')
guide_HomePlanet=train_test.loc[:,['Room','HomePlanet']].dropna().drop_duplicates('Room')
guide_Destination=train_test.loc[:,['Room','Destination']].dropna().drop_duplicates('Room')
train_test=pd.merge(train_test,guide_Cabin,how="left",on='Room',suffixes=('','_y'))
train_test=pd.merge(train_test,guide_VIP,how="left",on='Room',suffixes=('','_y'))
train_test=pd.merge(train_test,guide_HomePlanet,how="left",on='Room',suffixes=('','_y'))
train_test=pd.merge(train_test,guide_Destination,how="left",on='Room',suffixes=('','_y'))

In [32]:
train_test.loc[:,['VIP']]=train_test.apply(lambda x: x.VIP_y if pd.isna(x.VIP) else x,axis=1)
train_test.loc[:,['Cabin']]=train_test.apply(lambda x:  x.Cabin_y if pd.isna(x.Cabin) else x,axis=1)
train_test.loc[:,['HomePlanet']]=train_test.apply(lambda x:  x.HomePlanet_y if pd.isna(x.HomePlanet) else x,axis=1)
train_test.loc[:,['Destination']]=train_test.apply(lambda x:  x.Destination_y if pd.isna(x.Destination) else x,axis=1)

In [33]:
train_test[train_test.Cabin.isnull()]

PassengerId HomePlanet CryoSleep Cabin  Destination   Age    VIP  \
15        0012_01      Earth     False   NaN  TRAPPIST-1e  31.0  False   
93        0101_01       Mars      True   NaN  TRAPPIST-1e  31.0  False   
222       0239_01       Mars     False   NaN  TRAPPIST-1e  37.0  False   
272       0301_01      Earth      True   NaN  TRAPPIST-1e  16.0  False   
280       0310_01     Europa     False   NaN  TRAPPIST-1e  67.0  False   
...           ...        ...       ...   ...          ...   ...    ...   
12869     9058_01       Mars     False   NaN  TRAPPIST-1e  38.0    NaN   
12902     9138_01     Europa       NaN   NaN  TRAPPIST-1e  41.0  False   
12941     9223_01       Mars      True   NaN  TRAPPIST-1e  24.0  False   
12942     9223_02       Mars      True   NaN  TRAPPIST-1e  17.0  False   
12966     9269_01      Earth     False   NaN  TRAPPIST-1e  42.0  False   

       RoomService  FoodCourt  ShoppingMall     Spa  VRDeck  \
15            32.0        0.0         876.0     0.0     0.0   
93             0.0        0.0           0.0     0.0     0.0   
222          637.0        0.0           0.0    92.0   319.0   
272            0.0        0.0           0.0     0.0     0.0   
280            NaN      230.0           0.0  4476.0   241.0   
...            ...        ...           ...     ...     ...   
12869        784.0        0.0          42.0    38.0    10.0   
12902          0.0     1998.0           0.0  1023.0   867.0   
12941          0.0        0.0           0.0     0.0     0.0   
12942          0.0        0.0           0.0     0.0     0.0   
12966          0.0      847.0          17.0    10.0   144.0   

                    Name Transported  Expenses  Room Cabin_y  VIP_y  \
15         Justie Pooles       False     908.0  0012     NaN  False   
93             Book Trad        True       0.0  0101     NaN  False   
222         Diedow Resty       False    1048.0  0239     NaN  False   
272      Margia Wriggins       False       0.0  0301     NaN  False   
280     Naviton Coudered       False    4947.0  0310     NaN  False   
...                  ...         ...       ...   ...     ...    ...   
12869        Hammet Muff         NaN     874.0  9058     NaN    NaN   
12902  Misamak Trupistic         NaN    3888.0  9138     NaN  False   
12941         Weessh Sun         NaN       0.0  9223     NaN  False   
12942          Perit Sun         NaN       0.0  9223     NaN  False   
12966      Matty Scheron         NaN    1018.0  9269     NaN  False   

      HomePlanet_y Destination_y  
15           Earth   TRAPPIST-1e  
93            Mars   TRAPPIST-1e  
222           Mars   TRAPPIST-1e  
272          Earth   TRAPPIST-1e  
280         Europa   TRAPPIST-1e  
...            ...           ...  
12869         Mars   TRAPPIST-1e  
12902       Europa   TRAPPIST-1e  
12941         Mars   TRAPPIST-1e  
12942         Mars   TRAPPIST-1e  
12966        Earth   TRAPPIST-1e  

[162 rows x 20 columns]

In [34]:
fig,ax = plt.subplots(figsize=(30,10))
pd.set_option('display.max_rows', 100)
print(train_test.isnull().sum())
sns.heatmap(train_test.isnull())

PassengerId         0
HomePlanet        157
CryoSleep         174
Cabin             162
Destination       154
Age               270
VIP               172
RoomService       170
FoodCourt         180
ShoppingMall      175
Spa               177
VRDeck            177
Name                0
Transported      4277
Expenses            0
Room                0
Cabin_y           162
VIP_y             172
HomePlanet_y      157
Destination_y     154
dtype: int64


<AxesSubplot:>

### Age
### Yaş

In [35]:
fig, ax = plt.subplots(figsize=(15,5))
sns.heatmap(train_test.corr(),annot=True)

<AxesSubplot:>

In [36]:
fig, ax = plt.subplots(figsize=(15,5))
analys = train_test.loc[:,['Age','Expenses']]
ax.scatter(analys.Age,analys.Expenses)

In [37]:
pd.set_option('display.max_rows', 100)
print(train_test.isnull().sum())
sns.heatmap(train_test.isnull())

PassengerId         0
HomePlanet        157
CryoSleep         174
Cabin             162
Destination       154
Age               270
VIP               172
RoomService       170
FoodCourt         180
ShoppingMall      175
Spa               177
VRDeck            177
Name                0
Transported      4277
Expenses            0
Room                0
Cabin_y           162
VIP_y             172
HomePlanet_y      157
Destination_y     154
dtype: int64


<AxesSubplot:>

### HomePlanet + Destination.
### Ana Gezegen + Hedef.

In [38]:
analys = train_test.loc[:,['HomePlanet','Destination']]
analys['numeric'] =1
analys.groupby(['Destination','HomePlanet']).count()

numeric
Destination   HomePlanet         
55 Cancri e   Earth           995
              Europa         1343
              Mars            299
PSO J318.5-22 Earth          1083
              Europa           29
              Mars             68
TRAPPIST-1e   Earth          4737
              Europa         1780
              Mars           2328

In [39]:
pd.set_option('display.max_rows', 100)
print(train_test.isnull().sum())
sns.heatmap(train_test.isnull())

PassengerId         0
HomePlanet        157
CryoSleep         174
Cabin             162
Destination       154
Age               270
VIP               172
RoomService       170
FoodCourt         180
ShoppingMall      175
Spa               177
VRDeck            177
Name                0
Transported      4277
Expenses            0
Room                0
Cabin_y           162
VIP_y             172
HomePlanet_y      157
Destination_y     154
dtype: int64


<AxesSubplot:>

### Split Cabin.
### Bölünmüş Kabin.

In [40]:
train_test.loc[:,['Cabin_1']] = train_test.Cabin.str.split("/",expand=True).iloc[:,0]
train_test.loc[:,['Cabin_2']] = train_test.Cabin.str.split("/",expand=True).iloc[:,1]
train_test.loc[:,['Cabin_3']] = train_test.Cabin.str.split("/",expand=True).iloc[:,2]

In [41]:
train_test.loc[:,['FirstName']] = train_test.Name.str.split(" ",expand=True).iloc[:,0]
train_test.loc[:,['SecondName']] = train_test.Name.str.split(" ",expand=True).iloc[:,1]
train_test['Name_key']=train_test['SecondName']+train_test['Room']

### Let's apply SimpleImputer + OneHotEncoder.
### SimpleImputer + OneHotEncoder'ı uygulayalım.

In [42]:
num_cols = ['ShoppingMall','FoodCourt','RoomService','Spa','VRDeck','Expenses','Age']
cat_cols = ['CryoSleep','Cabin_1','Cabin_3','VIP','HomePlanet','Destination']
transported=['Transported']

In [43]:
train_test = train_test[num_cols+cat_cols+transported].copy()

In [44]:
num_imp = SimpleImputer(strategy='mean')
cat_imp = SimpleImputer(strategy='most_frequent')
ohe = OneHotEncoder (handle_unknown='ignore',sparse = False)

In [45]:
train_test[num_cols] = pd.DataFrame(num_imp.fit_transform(train_test[num_cols]),columns=num_cols)
train_test[cat_cols] = pd.DataFrame(cat_imp.fit_transform(train_test[cat_cols]),columns=cat_cols)
temp_train = pd.DataFrame(ohe.fit_transform(train_test[cat_cols]),columns= ohe.get_feature_names_out())
train_test = train_test.drop(cat_cols,axis=1)
train_test = pd.concat([train_test,temp_train],axis=1)

# Let's split train and test set.
# Tren ve test setini ayıralım.

In [46]:
train = train_test[train_test['Transported'].notnull()].copy()
train.Transported =train.Transported.astype('int')
test = train_test[train_test['Transported'].isnull()].drop("Transported",axis=1)

In [47]:
X = train.drop('Transported',axis=1)
y = train.Transported

In [48]:
X,y = shuffle(X,y)
X = X.reset_index(drop=True)
y = y.reset_index(drop=True)

In [49]:
print(get_score(xgb.XGBClassifier(**params_XGB_best),X,y).mean())

0.8042099687483448


# Let's deal with outliers.
# Aykırı değerlerle ilgilenelim.

In [50]:
features_isolation =['ShoppingMall','FoodCourt','RoomService','Spa','VRDeck','Age']

In [51]:
from sklearn.ensemble import IsolationForest

isf = IsolationForest(n_jobs=-1, random_state=1,n_estimators=100,contamination=0.003)
isf.fit(X[features_isolation], y)

rows = pd.DataFrame(isf.predict(X[features_isolation]),columns=['feature'])
rows_ind = rows[rows.feature == 1]
results = pd.DataFrame()
results['results'] = - isf.score_samples(X[features_isolation])
results['chance'] = isf.decision_function(X[features_isolation])
results['yes/no'] = isf.predict(X[features_isolation])

new = results[results['yes/no']==1]
old= results[results['yes/no']==-1]
fig,ax = plt.subplots(figsize=(20,10))
ax.set_facecolor('black')
ax = plt.scatter(new.index,new.results,marker=".")
ax = plt.scatter(old.index,old.results,color='white',marker="*")

In [52]:
X_1 = X.iloc[rows_ind.index].reset_index(drop=True)
y_1 = y.iloc[rows_ind.index].reset_index(drop=True) 
print(get_score(xgb.XGBClassifier(**params_XGB_best),X_1,y_1).mean())

0.8041724758144337


In [53]:
fig = plt.subplots(figsize=(30,10))   
sns.heatmap(train.corr(),annot=True)

<AxesSubplot:>

In [54]:
params_XGB_best= {'lambda': 3.0610042624477543, 
             'alpha': 4.581902571574289, 
             'colsample_bytree': 0.9241969052729379, 
             'subsample': 0.9527591724824661, 
             'learning_rate': 0.06672065863100594, 
             'n_estimators': 725, #initial value is 651
             'max_depth': 5, 
             'min_child_weight': 1, 
             'num_parallel_tree': 1}

In [55]:
perm = PermutationImportance(xgb.XGBClassifier(**params_XGB_best), random_state=1,n_iter =10,cv=5).fit(X, y)
eli5.show_weights(perm, feature_names = X.columns.tolist(),top=50)

In [56]:
drop_list=['ShoppingMall','Age','CryoSleep_True','HomePlanet_Earth','HomePlanet_Europa',
'VIP_True','HomePlanet_Mars','Destination_PSO J318.5-22','VIP_False',
'Destination_55 Cancri e','FoodCourt','Destination_TRAPPIST-1e']

In [57]:
X=X.drop(drop_list,axis=1)
test=test.drop(drop_list,axis=1)


In [58]:
print(get_score(xgb.XGBClassifier(**params_XGB_best),X,y).mean())

0.8082390486784258


In [59]:
from imblearn.over_sampling import SMOTE

In [60]:
smote = SMOTE(sampling_strategy=1, n_jobs=-1)
X_sm, y_sm = smote.fit_resample(X, y)
X = X_sm
y = y_sm

In [61]:
y.value_counts()

0    4378
1    4378
Name: Transported, dtype: int64

# Modeling
# Modelleme

In [62]:
optuna_study = "ON"
LGBM_study = "OFF"
XGB_study = "OFF"
CAT_study = "OFF"


gpu_switch = "OFF"
skf = StratifiedKFold(n_splits=10)

## LGBM

In [63]:
if gpu_switch == "ON":
    method = "gpu"
else:
    method = "cpu"

def objective(trial):
    param = {
     'objective': 'binary',
     'device': method,
     'metric': 'binary_logloss',
     'verbosity': -1,
     'lambda_l1': trial.suggest_float('lambda_l1', 1e-8, 10.0),
     'lambda_l2': trial.suggest_float('lambda_l2', 1e-8, 10.0),
     'learning_rate': trial.suggest_float('learning_rate', 0.0001,0.1),
     'num_leaves': trial.suggest_int('num_leaves', 2, 512),
     'feature_fraction': trial.suggest_float('feature_fraction', 0.4, 1.0),
     'bagging_fraction': trial.suggest_float('bagging_fraction', 0.4, 1.0),
     'bagging_freq': trial.suggest_int('bagging_freq', 1, 7),
     'min_child_samples': trial.suggest_int('min_child_samples', 5, 100),
     'n_estimators' : trial.suggest_int('n_estimators', 100, 20000),
     'subsample':None,
     'subsample_freq':None,
     'reg_alpha':None,
     'colsample_bytree':None,
     'reg_lambda':None,
     'early_stopping_round':trial.suggest_int('early_stopping_round', 200, 200)
            }
    results=[]
    n_iterations=[]
    for train_index, test_index in skf.split(X, y):
        train_X, valid_X = X.iloc[train_index], X.iloc[test_index]
        train_y, valid_y = y.iloc[train_index], yi.loc[test_index]
        model = lgb.LGBMClassifier(**param).fit(train_X,train_y,
                                            eval_set=[(valid_X,valid_y)],
                                            callbacks=[lgb.log_evaluation(period=0, show_stdv=False)]
                                             )  
        n_iteration = model.best_iteration_
        n_iterations.append(n_iteration)
        result = accuracy_score(valid_y,(model.predict(valid_X)))
        results.append(result)
        i=int(sum(n_iterations)/len(n_iterations))
    print("Average n_ite=" + str(i))
    print("% of scatter =" + str(np.std(n_iterations)/i))
    n=sum(results)/len(results)
    print(n)
    print("FIIINISH__________________________________\n")
       
    return n

if optuna_study == LGBM_study:
    study = optuna.create_study(pruner=optuna.pruners.HyperbandPruner(),
                                direction='maximize')
    study.optimize(objective, n_trials=10000)
    print('Best trial:', study.best_trial.params)

### Trial 1468 finished with value: 0.8084681392022881
### Deneme 1468 şu değerle tamamlandı: 0.8084681392022881

In [64]:
params_LGBM= {'lambda_l1': 6.183557865875619, 
              'lambda_l2': 0.011470762415538793, 
              'learning_rate': 0.08693013162698361, 
              'num_leaves': 330,
              'feature_fraction': 0.6583455294128855, 
              'bagging_fraction': 0.8666491286986552, 
              'bagging_freq': 1, 
              'min_child_samples': 17, 
              'n_estimators': 739}

In [65]:
if gpu_switch == "ON":
    method = "gpu_hist"
else:
    method = "hist"

def objective(trial):
    print("START__________________________________")
    param = {  
        'tree_method':method,
        'objective': 'binary:logistic',
        'eval_metric': 'logloss',
        'lambda': trial.suggest_float('lambda', 0, 10.0),
        'alpha': trial.suggest_float('alpha', 0, 10.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.1,1.0),
        'subsample': trial.suggest_float('subsample', 0.2,1.0),
        'learning_rate': trial.suggest_float('learning_rate', 0.0001,0.1),
        'n_estimators': trial.suggest_int('n_estimators', 100,3000),
        'max_depth': trial.suggest_categorical('max_depth', [2,3,4,5,6,7,8,9,10]),
        'min_child_weight': trial.suggest_int('min_child_weight', 1, 10),
        'num_parallel_tree': trial.suggest_int('num_parallel_tree',1,1),
        'early_stopping_rounds':200,
        }
    
    results=[]
    n_iterations=[]
    for train_index, test_index in skf.split(X, y):
        train_X, valid_X = X.iloc[train_index], X.iloc[test_index]
        train_y, valid_y = y.iloc[train_index], y.iloc[test_index]
        model = xgb.XGBClassifier(**param).fit(train_X,train_y,
                                      eval_set=[(valid_X,valid_y)],
                                      verbose=0
                                     )  

        result = accuracy_score(valid_y,(model.predict(valid_X)))
        results.append(result)
  
    n=sum(results)/len(results) 
    print (n)
    print("FIIINISH__________________________________\n")
    return n

if optuna_study == XGB_study:
    study = optuna.create_study(pruner=optuna.pruners.HyperbandPruner(),
                                direction='maximize')
    study.optimize(objective, n_trials=1000)

### Trial 82 finished with value: 0.8107728163567985
### Deneme 82 şu değerle tamamlandı: 0.8107728163567985

In [66]:
params_XGB_best= {'lambda': 3.0610042624477543, 
             'alpha': 4.581902571574289, 
             'colsample_bytree': 0.9241969052729379, 
             'subsample': 0.9527591724824661, 
             'learning_rate': 0.06672065863100594, 
             'n_estimators': 730, #initial value is 651
             'max_depth': 5, 
             'min_child_weight': 1, 
             'num_parallel_tree': 1}
#Average n_ite=661

In [67]:
pred_XGB_best = (xgb.XGBClassifier(**params_XGB_best).fit(X,y)).predict(test)
sample['Transported'] = pred_XGB_best
sample['Transported']=sample['Transported']>0.5
sample.to_csv('serkan.csv', index=False)